Importanto bibliotecas

In [19]:
import folium
import geopandas as gpd
import pandas as pd
import json
import numpy as np
from branca.element import Html

Lendo arquivos

In [20]:
pe = gpd.read_file('pop_pe_2010_2022.gpkg')
pe.to_file('pe.geojson', driver="GeoJSON")
pe_json = gpd.read_file('pe.geojson')

Transformando para json e classificando por quartis

In [21]:
with open('pe.geojson', 'r', encoding="utf8") as f:
    geojson_data = json.load(f)

valores = [feature['properties']['POP_2022'] for feature in geojson_data['features']]

quartis = pd.qcut(valores, 4, labels=['1º Quartil', '2º Quartil', '3º Quartil', '4º Quartil'])

for feature, quartil in zip(geojson_data['features'], quartis):
    feature['properties']['quartil'] = quartil


In [22]:
# Dicionário de cores para cada quartil
cores_quartis = {
    '1º Quartil': '#ffffb2',  # Amarelo claro
    '2º Quartil': '#fecc5c',  # Laranja claro
    '3º Quartil': '#fd8d3c',  # Laranja médio
    '4º Quartil': '#e31a1c'   # Vermelho
}

# Função de estilo para os polígonos
def estilo_quartil(feature):
    return {
        'fillColor': cores_quartis[feature['properties']['quartil']],
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.7
    }


Mapa

In [25]:
# Criar o mapa
mapa = folium.Map(location=[-8.3, -38.0], zoom_start=8)


# Adicionar o GeoJSON ao mapa com o estilo
folium.GeoJson(
    geojson_data,
    style_function=estilo_quartil,
    tooltip=folium.features.GeoJsonTooltip(fields=['NM_MUN','POP_2010', 'POP_2022', 'AREA_KM2'], 
                                           aliases=['Município:', 'População de 2010:', 'População de 2022:',
                                                   'Área km²:'], style=("font-size: 16px;"), localize= True)
).add_to(mapa)

# Exibir o mapa
mapa

Salvar mapa

In [26]:
mapa.save('mapa_pernambuco_populacao.html')
